# Webscrapping de l'indice VIX

## Obtenir la bonne page HTML avec Selenium

Avant de commencer le webscrapping, nous devons effectuer quelques modifications dans le code HMTML de base de la pgae web. Ainsi, pour obtenir le jeu de données entier, nous allons utiliser la librairie **selenium** qui nous permettra d'obtenir la page HTML avec toutes les données.

In [1]:
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait 
from selenium.webdriver.support import expected_conditions as EC


In [2]:
import time
driver = webdriver.Chrome(ChromeDriverManager().install())#,options=chrome_options)
driver.get('https://fr.investing.com/indices/volatility-s-p-500-historical-data')
WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.ID, "onetrust-accept-btn-handler"))).click()

#elements =driver.find_elements(By.CSS_SELECTOR,'css-1545rns-container')
dropdown =driver.find_element("id",'history-timeframe-selector')
dropdown.click() # on ouvre le dropdown

# on cherche les différentes options présentes dans le dropdown et on clique sur celle qu'on veut
driver.find_element("id","react-select-2-option-0").click() # 0 -> journalier, 1 -> Hebdomadaire, 2 -> pour Mensuel 

calendar=driver.find_element(By.CLASS_NAME,"historical-data_history-date-picker-wrapper__dDOuq")
calendar.click()

date_input = driver.find_element(By.XPATH,'/html/body/div[1]/div/div/div/div[2]/main/div/div[5]/div/div/div[2]/div[2]/div[2]/div[2]/div[1]/div/div[1]/input')
date_input.clear()
date_input.send_keys("3004-08-2005") #date à laquelle on souhaite commencer (marche pas mais permet de donner tout l'historique pour l'instant)


validate=driver.find_element(By.CLASS_NAME,"HistoryDatePicker_arrow-icon__NwxN4")
validate.click()
time.sleep(6)

#driver.find_element(By.CLASS_NAME,"inv-button signup_close__MFV87").click()

#WebDriverWait(driver, 20).until(EC.element_to_be_clickable((By.CLASS_NAME,"inv-button signup_close__MFV87"))).click() # on attend 10 secondes avant de break en l'abscence du bouton


time.sleep(6)

webpage=driver.page_source # on stock le code html de la page où toutes le données sont chargées
#driver.quit()  



[WDM] - Downloading: 100%|██████████| 6.46M/6.46M [00:04<00:00, 1.54MB/s]
C:\Users\elelo\AppData\Local\Temp/ipykernel_14624/3537833647.py:2: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())#,options=chrome_options)


## From HTML to Dataframe :

Maintenant que nous avons le code HTML de toutes les données, nous allons décortiquer la page grâce à la librairie BeautifulSoup.

In [3]:
import bs4
import pandas

In [4]:
# utiliser le package BeautifulSoup qui "comprend" les balises 

page = bs4.BeautifulSoup(webpage, "lxml")

print(page)

<html class="html" dir="ltr" lang="fr"><head><script async="" src="https://www.googletagmanager.com/gtm.js?id=GTM-PGT3R3D&amp;l=dataLayerGTMParams"></script><script async="" gtm="GTM-PGT3R3D" src="https://www.googleoptimize.com/optimize.js?id=GTM-WW3TL3X&amp;l=dataLayerGTMParams" type="text/javascript"></script><script async="" src="https://connect.facebook.net/en_US/fbevents.js"></script><script async="" src="https://www.googletagmanager.com/gtag/js?id=G-C4NDLGKVMK&amp;l=dataLayerGTMParams&amp;cx=c" type="text/javascript"></script><script async="" src="https://www.google-analytics.com/analytics.js" type="text/javascript"></script><script>
                window.geo_country = 'FR';
                window.geo_state = 'IDF';
            </script>
<script charset="UTF-8" data-domain-script="265d5ac2-7d0c-4675-bf4d-421a61fb482e" src="https://cookie-cdn.cookiepro.com/scripttemplates/otSDKStub.js" type="text/javascript"></script>
<meta charset="utf-8"/><meta content="initial-scale=1.0, width

In [5]:
# on identifie le tableau des indices vix : c'est le premier qui a cette classe "datatable_table__D_jso datatable_table--border__B_zW0 datatable_table--mobile-basic__W2ilt datatable_table--freeze-column__7YoIE"
tableau_indice = page.find('table', {'class' : 'datatable_table__D_jso datatable_table--border__B_zW0 datatable_table--mobile-basic__W2ilt datatable_table--freeze-column__7YoIE'})


In [6]:
table_body = tableau_indice.find('tbody')

# on recherche toutes les lignes du tableau avec la balise "tr"
rows = table_body.find_all('tr')

# on obtient une liste où chaque élément est une des lignes du tableau



In [7]:
cols = rows[0].find_all('td')
print(cols[0])
print(cols[0].text.strip())

<td class="datatable_cell__0y0eu font-bold"><time datetime="05/12/2022">05/12/2022</time></td>
05/12/2022


Voici le dictionnaire de tous les indices VIX :

In [8]:
dico_vix = dict()
for row in rows:
    cols = row.find_all('td')
    cols = [ele.text.strip() for ele in cols]
    if len(cols) > 0 : 
        dico_vix[cols[0]] = cols[1:]
dico_vix

{'05/12/2022': ['20,26', '20,30', '20,32', '20,25', '', '+6.30%'],
 '02/12/2022': ['19,06', '20,42', '20,96', '18,95', '', '-3.93%'],
 '01/12/2022': ['19,84', '20,83', '21,06', '19,80', '', '-3.60%'],
 '30/11/2022': ['20,58', '21,70', '22,63', '20,31', '', '-5.98%'],
 '29/11/2022': ['21,89', '22,09', '22,57', '21,83', '', '-1.44%'],
 '28/11/2022': ['22,21', '22,09', '22,50', '21,65', '', '+8.34%'],
 '25/11/2022': ['20,50', '20,61', '21,11', '20,46', '', '+0.39%'],
 '24/11/2022': ['20,42', '20,50', '20,54', '20,31', '', '+0.34%'],
 '23/11/2022': ['20,35', '21,49', '21,78', '20,32', '', '-4.42%'],
 '22/11/2022': ['21,29', '22,59', '22,71', '21,28', '', '-4.79%'],
 '21/11/2022': ['22,36', '24,05', '24,12', '22,30', '', '-3.29%'],
 '18/11/2022': ['23,12', '24,03', '24,12', '22,98', '', '-3.38%'],
 '17/11/2022': ['23,93', '24,05', '25,18', '23,81', '', '-0.75%'],
 '16/11/2022': ['24,11', '24,29', '24,72', '23,99', '', '-1.75%'],
 '15/11/2022': ['24,54', '23,77', '26,22', '23,18', '', '+3.41

In [9]:
data_vix = pandas.DataFrame.from_dict(dico_vix,orient='index')
data_vix.head()

0      1      2      3 4       5
05/12/2022  20,26  20,30  20,32  20,25    +6.30%
02/12/2022  19,06  20,42  20,96  18,95    -3.93%
01/12/2022  19,84  20,83  21,06  19,80    -3.60%
30/11/2022  20,58  21,70  22,63  20,31    -5.98%
29/11/2022  21,89  22,09  22,57  21,83    -1.44%

In [10]:
data_vix=data_vix.rename(columns={0:"dernier_vix",1:'ouverture',2:'higher',3:'lower',4:'volatilité',5:'variation'})
data_vix=data_vix.drop(columns=['volatilité'])

In [11]:
data_vix

dernier_vix ouverture higher  lower variation
05/12/2022       20,26     20,30  20,32  20,25    +6.30%
02/12/2022       19,06     20,42  20,96  18,95    -3.93%
01/12/2022       19,84     20,83  21,06  19,80    -3.60%
30/11/2022       20,58     21,70  22,63  20,31    -5.98%
29/11/2022       21,89     22,09  22,57  21,83    -1.44%
...                ...       ...    ...    ...       ...
05/05/2005       13,98     13,48  15,82  13,43    +0.94%
04/05/2005       13,85     14,44  15,38  13,70    -4.68%
03/05/2005       14,53     15,19  15,31  14,53    -3.90%
02/05/2005       15,12     15,45  16,01  15,08    -1.24%
29/04/2005       15,31     15,75  16,92  15,26    -9.19%

[4445 rows x 5 columns]

In [12]:
def replace_comma_to_float(text):
    return float(text.replace(',','.'))

data_vix["dernier_vix"]=data_vix["dernier_vix"].apply(replace_comma_to_float)
data_vix["ouverture"]=data_vix["ouverture"].apply(replace_comma_to_float)
data_vix["higher"]=data_vix["higher"].apply(replace_comma_to_float)
data_vix["lower"]=data_vix["lower"].apply(replace_comma_to_float)

In [13]:
data_vix["date"]=data_vix.index
data_vix.reset_index(drop=True, inplace=True)


In [14]:
#convertir la date str au format date

from datetime import datetime

data_vix["date"]=data_vix['date'].apply(lambda x : datetime.strptime(x, '%d/%m/%Y'))

In [15]:
data_vix.to_csv("data_vix.csv",index=False)